# Project Steam

> Utilisation: ce notebook est destiné à fonctionnner dans l'environnement **Databriks** ONLY!

## Loading raw dataset

In [0]:
# Imports used withing that notebook
from pyspark.sql import functions as F
from pyspark.sql.types import *

In [0]:
steam_dataset_path = "s3://full-stack-bigdata-datasets/Big_Data/Project_Steam/steam_game_output.json"

raw_df = spark.read.json(steam_dataset_path)

print("Original Stream dataset loaded.")

Original Stream dataset loaded.


## Schema walkthrough

In [0]:
raw_df.count()

55691

In [0]:
raw_df.columns

['data', 'id']

In [0]:
raw_df.printSchema()

root
 |-- data: struct (nullable = true)
 |    |-- appid: long (nullable = true)
 |    |-- categories: array (nullable = true)
 |    |    |-- element: string (containsNull = true)
 |    |-- ccu: long (nullable = true)
 |    |-- developer: string (nullable = true)
 |    |-- discount: string (nullable = true)
 |    |-- genre: string (nullable = true)
 |    |-- header_image: string (nullable = true)
 |    |-- initialprice: string (nullable = true)
 |    |-- languages: string (nullable = true)
 |    |-- name: string (nullable = true)
 |    |-- negative: long (nullable = true)
 |    |-- owners: string (nullable = true)
 |    |-- platforms: struct (nullable = true)
 |    |    |-- linux: boolean (nullable = true)
 |    |    |-- mac: boolean (nullable = true)
 |    |    |-- windows: boolean (nullable = true)
 |    |-- positive: long (nullable = true)
 |    |-- price: string (nullable = true)
 |    |-- publisher: string (nullable = true)
 |    |-- release_date: string (nullable = true)
 |    |-

On a 2 propriétés racines: "data" et "id".

- "**data**" est une structure complexe.
- "**id**" est une chaine de caratères

**data**

On voit que le champs **tags** est une structure un peu particulière (une propriété = 1 tag avec en valeur le nombre de fois ou le l'application a été taggée avec celui-ci). Par ailleurs, compte tenu des attentes de l'analyse il semble envisageable d'ignorer ce champ pour la suite.

In [0]:
# A quoi ressemble le schéma imbriqué de "data"
print(f"{'Propriété':<20} | Type")
print(f"{'-'*20} | {'-'*10}")

for field in raw_df.schema["data"].dataType.fields:
    print(f"{field.name:<20} | {type(field.dataType).__name__}")

Propriété            | Type
-------------------- | ----------
appid                | LongType
categories           | ArrayType
ccu                  | LongType
developer            | StringType
discount             | StringType
genre                | StringType
header_image         | StringType
initialprice         | StringType
languages            | StringType
name                 | StringType
negative             | LongType
owners               | StringType
platforms            | StructType
positive             | LongType
price                | StringType
publisher            | StringType
release_date         | StringType
required_age         | StringType
short_description    | StringType
tags                 | StructType
type                 | StringType
website              | StringType


In [0]:
from pyspark.sql.types import StructType, StructField
from typing import List, Dict, Generator, Union, Callable

def walkSchema(schema: Union[StructType, StructField], exclude: List[str] = []) -> Generator[str, None, None]:
    """Explores a PySpark schema:
    
    schema: StructType | StructField
    
    Yield
    -----
    A generator of strings, the name of each field in the schema
    """

    # some keys may have a dot in there name. This function aim to escape properly those ones if encountered.
    def _sanitizedKeyName(name: str):
        if '.' in name:
            return f"`{name}`"
        return name

    # we define a function _walk that produces a string generator from
    # a dictionnary "schema_dct", and a string "prefix"
    def _walk(schema_dct: Dict['str', Union['str', list, dict]],
              prefix: str = "", exclude: List[str] = []) -> Generator[str, None, None]:
        assert isinstance(prefix, str), "prefix should be a string" # check if prefix is a string

        if prefix in exclude:
            print(f"!! -> prefix {prefix} is exluded")
            return
        
        # this function returns "name" if there's no prefix and "prefix.name" if prefix exists
        fullName: Callable[str, str] = lambda name: ( 
            _sanitizedKeyName(name) if not prefix else f"{prefix}.{_sanitizedKeyName(name)}")
        
        # we get the next name one level lower from the dictionnary
        name = schema_dct.get('name', '')

        # if the type is struct then we search for the fields key
        # if fields is there we apply the function again and dig one level deeper in
        # the schema and set a prefix
        if schema_dct['type'] == 'struct':
            assert 'fields' in schema_dct, (
                "It's a StructType, we should have some fields")
            for field in schema_dct['fields']:
                yield from _walk(field, prefix=prefix, exclude=exclude)
        if schema_dct['type'] == 'array':
            # {'type': 'array', 'elementType': 'string', 'containsNull': True}
            elementType = schema_dct['elementType']
            if elementType == 'dict' or elementType == 'dict':
                print(f"Array type '{elementType}' not handled")
            else:
                # base type, map array as is
                yield prefix
        # if we have a dict type and we can't find fields then we
        # dig one level deeper and apply the _walk function again
        elif isinstance(schema_dct['type'], dict):
            assert 'fields' not in schema_dct, (
                "We're missing some keys here")
            yield from _walk(schema_dct['type'], prefix=fullName(name), exclude=exclude)
        # If we finally reached the end and found a name we yield the full name
        elif name:
            yield fullName(name)
    
    yield from _walk(schema.jsonValue(), exclude=exclude)


In [0]:
for col_name in walkSchema(raw_df.schema, exclude =["data.tags"]):
  print(col_name)

data.appid
data.categories
data.ccu
data.developer
data.discount
data.genre
data.header_image
data.initialprice
data.languages
data.name
data.negative
data.owners
data.platforms.linux
data.platforms.mac
data.platforms.windows
data.positive
data.price
data.publisher
data.release_date
data.required_age
data.short_description
!! -> prefix data.tags is exluded
data.type
data.website
id


In [0]:
# display(raw_df.limit(5).toPandas())

In [0]:

# Regardons un enregistrement
raw_df.select(F.col('id'), F.col('data')).take(1)

[Row(id='10', data=Row(appid=10, categories=['Multi-player', 'Valve Anti-Cheat enabled', 'Online PvP', 'Shared/Split Screen PvP', 'PvP'], ccu=13990, developer='Valve', discount='0', genre='Action', header_image='https://cdn.akamai.steamstatic.com/steam/apps/10/header.jpg?t=1666823513', initialprice='999', languages='English, French, German, Italian, Spanish - Spain, Simplified Chinese, Traditional Chinese, Korean', name='Counter-Strike', negative=5199, owners='10,000,000 .. 20,000,000', platforms=Row(linux=True, mac=True, windows=True), positive=201215, price='999', publisher='Valve', release_date='2000/11/1', required_age='0', short_description="Play the world's number 1 online action game. Engage in an incredibly realistic brand of terrorist warfare in this wildly popular team-based game. Ally with teammates to complete strategic missions. Take out enemy sites. Rescue hostages. Your role affects your team's success. Your team's success affects your role.", tags=Row(1980s=266, 1990's=

In [0]:
# C'est quoi ce data.type?
c_df = raw_df.groupBy("data.type").count()
c_df.show()

+--------+-----+
|    type|count|
+--------+-----+
|hardware|    1|
|    game|55690|
+--------+-----+



Ce qui nous intéresse ce sont les jeux.

In [0]:
# ip == appid ?
raw_df.filter(F.col("id") != F.col("data.appid")).count()

0

On peut ne considérer que le contenu de `data` puisque `id` est bien une réplique de `appid` lui-même contenu dans `data`.

## Préparation d'un dataset adapté

In [0]:
# Transforming a few columns
# languages: from comma separated list to array (ex.: "languages": "Simplified Chinese, English, Traditional Chinese, Japanese, Korean",)
# genres: from comma separated list to array 
# release_date: as Date ("release_date": "2019/06/24")

raw_df_columns_remap = {
  "appid": F.col("data.appid"),
  "ccu": F.col("data.ccu"),
  "categories": F.col("data.categories"),
  "developer": F.col("data.developer"),
  "genres": F.split("data.genre", ",\s*"),
  "name": F.col("data.name"),
  "initial_price": F.col("data.initialprice"),
  "price": F.col("data.price"),
  "discount": F.col("data.discount"),
  "positive_ratings": F.col('data.positive'),
  "negative_ratings": F.col('data.negative'),
  "publisher": F.col("data.publisher"),
  "release_date": F.to_date(F.col("data.release_date"), 'yyyy/MM/d'),
  "has_linux_support": F.col("data.platforms.linux"),
  "has_mac_support": F.col("data.platforms.mac"),
  "has_windows_support": F.col("data.platforms.windows"),
  "owners": F.col("data.owners"),
  "languages": F.split("data.languages", ",\s*"),
  "required_age": F.col("data.required_age"),
  "type": F.col('data.type'),
}
# Some casts may be used later:
# discount -> cast(DoubleType())) 
# price -> cast(DoubleType())) 
# initialprice -> cast(DoubleType())) 
# required_age -> cast(IntegerType()

# 1. mapping des colonnes du schéma imbriqué
# 2. cast de quelques valeures (numérique, date)
# 3. filtrer pour ne garder que les jeux
steam_games_df = raw_df.withColumns(raw_df_columns_remap).drop('data').filter(F.col('type') == 'game')

steam_games_df.count()


55690

In [0]:
display(steam_games_df.take(5))

id appid ccu categories developer genres name initial_price price discount positive_ratings negative_ratings publisher release_date has_linux_support has_mac_support has_windows_support owners languages required_age type 10 10 13990 List(Multi-player, Valve Anti-Cheat enabled, Online PvP, Shared/Split Screen PvP, PvP) Valve List(Action) Counter-Strike 999 999 0 201215 5199 Valve 2000-11-01 true true true 10,000,000 .. 20,000,000 List(English, French, German, Italian, Spanish - Spain, Simplified Chinese, Traditional Chinese, Korean) 0 game 1000000 1000000 0 List(Single-player, Partial Controller Support, Steam Achievements, Steam Cloud) IndigoBlue Game Studio List(Action, Adventure, Indie) ASCENXION 999 999 0 27 5 PsychoFlux Entertainment 2021-05-14 false false true 0 .. 20,000 List(English, Korean, Simplified Chinese) 0 game 1000010 1000010 99 List(Single-player, Partial Controller Support, Steam Achievements, Steam Cloud, Steam Trading Cards) NEXT Studios List(Adventure, Indie, RPG, Strategy) Crown Trick 1999 599 70 4032 646 Team17, NEXT Studios 2020-10-16 false false true 200,000 .. 500,000 List(Simplified Chinese, English, Japanese, Traditional Chinese, French, German, Spanish - Spain, Russian, Portuguese - Brazil) 0 game 1000030 1000030 76 List(Multi-player, Single-player, Co-op, Steam Achievements, Steam Cloud, Shared/Split Screen, Full controller support, Steam Trading Cards, Shared/Split Screen Co-op, Remote Play on Phone, Remote Play on Tablet, Remote Play on TV, Remote Play Together) Vertigo Gaming Inc. List(Action, Indie, Simulation, Strategy) Cook, Serve, Delicious! 3?! 1999 1999 0 1575 115 Vertigo Gaming Inc. 2020-10-14 false true true 100,000 .. 200,000 List(English) 0 game 1000040 1000040 0 List(Single-player) DoubleC Games List(Action, Casual, Indie, Simulation) 细胞战争 199 199 0 0 1 DoubleC Games 2019-03-30 false false true 0 .. 20,000 List(Simplified Chinese) 0 game

In [0]:
def build_null_or_empty_check(column, dtype):
    if dtype == "string":
        # for string let also check for empty strings
        return F.when(F.isnull(column) | (F.trim(F.col(column)) == ''), column)

    return F.when(F.isnull(column), column)
    
steam_games_df.select([F.count(build_null_or_empty_check(c, t)).alias(c) for c, t in steam_games_df.dtypes]).show()

+---+-----+---+----------+---------+------+----+-------------+-----+--------+----------------+----------------+---------+------------+-----------------+---------------+-------------------+------+---------+------------+----+
| id|appid|ccu|categories|developer|genres|name|initial_price|price|discount|positive_ratings|negative_ratings|publisher|release_date|has_linux_support|has_mac_support|has_windows_support|owners|languages|required_age|type|
+---+-----+---+----------+---------+------+----+-------------+-----+--------+----------------+----------------+---------+------------+-----------------+---------------+-------------------+------+---------+------------+----+
|  0|    0|  0|         0|      126|     0|   0|            0|    0|       0|               0|               0|      134|         222|                0|              0|                  0|     0|        0|           0|   0|
+---+-----+---+----------+---------+------+----+-------------+-----+--------+----------------+----------

Il nous manque quelques dates de release
Tous les developpeurs et éditeurs ne sont pas renseignés (on pourra toujours tenter de remplacer l'un par l'autre en cas de valeur absente)

In [0]:
# Check: on peut voir que c'est le empty qui faisait office de "non renseigné"
print("Check des valeurs non renseignées (isnull):")
steam_games_df.select([F.count(F.when(F.isnull("publisher"), "publisher")).alias("publisher"), F.count(F.when(F.isnull("developer"), "developer")).alias("developer")]).show()

# On s'assure que publisher et developper sont NULL quand non renseignés. Cela simplifiera l'usage du coalesce plus tard.
columns_nullifying_on_empty = {
    "publisher": F.when(F.trim(F.col("publisher"))=="", None).otherwise(F.trim(F.col("publisher"))),
    "developer": F.when(F.trim(F.col("developer")) == "", None).otherwise(F.trim(F.col("developer"))),
}

# Adaptation du DataFrame
steam_games_df = steam_games_df.withColumns(columns_nullifying_on_empty)

# Check de validation
print("Check des valeurs non renseignées (isnull) aprés update du DataFrame:")
steam_games_df.select([F.count(F.when(F.isnull("publisher"), "publisher")).alias("publisher"), F.count(F.when(F.isnull("developer"), "developer")).alias("developer")]).show()


Check des valeurs non renseignées (isnull):
+---------+---------+
|publisher|developer|
+---------+---------+
|        0|        0|
+---------+---------+

Check des valeurs non renseignées (isnull) aprés update du DataFrame:
+---------+---------+
|publisher|developer|
+---------+---------+
|      134|      126|
+---------+---------+



In [0]:
steam_games_df.select([F.count(build_null_or_empty_check(c, t)).alias(c) for c, t in steam_games_df.dtypes]).show()

+---+-----+---+----------+---------+------+----+-------------+-----+--------+----------------+----------------+---------+------------+-----------------+---------------+-------------------+------+---------+------------+----+
| id|appid|ccu|categories|developer|genres|name|initial_price|price|discount|positive_ratings|negative_ratings|publisher|release_date|has_linux_support|has_mac_support|has_windows_support|owners|languages|required_age|type|
+---+-----+---+----------+---------+------+----+-------------+-----+--------+----------------+----------------+---------+------------+-----------------+---------------+-------------------+------+---------+------------+----+
|  0|    0|  0|         0|      126|     0|   0|            0|    0|       0|               0|               0|      134|         222|                0|              0|                  0|     0|        0|           0|   0|
+---+-----+---+----------+---------+------+----+-------------+-----+--------+----------------+----------

## Analyse macro

* Quels sont les éditeurs ayant publié le plus de jeux sur Steam ?
* Quels sont les jeux les mieux notés ?
* Y a-t-il des années avec un nombre plus élevé de sorties ? La pandémie de Covid a-t-elle eu un impact sur le volume de publications ?
* Comment les prix sont-ils répartis ? Y a-t-il beaucoup de jeux en promotion ?
* Quelles sont les langues les plus représentées ?
* Combien de jeux sont interdits aux moins de 16 ou 18 ans ?


### Quels sont les éditeurs ayant publié le plus de jeux sur Steam ?


In [0]:
# .select(F.coalesce("publisher", "developer").alias("publisher")) \
publisher_df = steam_games_df \
        .select("publisher") \
        .distinct() \
        .count()

print("Nombre d'editeurs :")
display(publisher_df)
print()

result_df = steam_games_df \
        .select(F.coalesce("publisher", "developer").alias("publisher")) \
        .groupBy("publisher").agg(F.count("*").alias("games_count")) \
        .orderBy(F.desc("games_count")) \
        .limit(10)

print("Top 10 des publications de jeux par editeurs :")
display(result_df)

Nombre d'editeurs :


29834


Top 10 des publications de jeux par editeurs :


publisher games_count Big Fish Games 423 8floor 202 SEGA 165 Strategy First 151 Square Enix 141 Choice of Games 140 Sekai Project 132 HH-Games 132 Ubisoft 127 Laush Studio 126

Databricks visualization. Run in Databricks to view.

#### Analyse

L'éditeur le plus représenté sur Steam est [**Big Fish Games**](https://en.wikipedia.org/wiki/Big_Fish_Games) avec au catalogue 423 jeux.


### Quels sont les jeux les mieux notés ?

Un ancien article propose une formule pour évaluation plus juste des scores (ref. : https://steamdb.info/blog/steamdb-rating/).
Ce classement l'utilisera.

$$(Total Reviews = Positive Reviews + Negative Reviews)$$

$$( Review Score = \frac{Positive Reviews}{Total Reviews} )$$

$$( Rating = Review Score - (Review Score - 0.5)*2^{-log_{10}(Total Reviews + 1)} )$$


In [0]:
result_df = steam_games_df \
        .withColumn("total_ratings", F.col("positive_ratings") + F.col("negative_ratings")) \
        .withColumn("rating_score", F.col("positive_ratings") / F.col("total_ratings")) \
        .withColumn("rating", F.round(100 * (F.col("rating_score") - (F.col("rating_score") - 0.5) * F.pow(2, -F.log10(F.col("total_ratings") + 1))), 2))

print("Top 20 des jeux sur Steam :")
display(result_df.select("name", "rating", "price", "positive_ratings", "negative_ratings", "publisher").orderBy(F.desc("rating")).limit(20))

Top 20 des jeux sur Steam :


name rating price positive_ratings negative_ratings publisher Portal 2 97.7 999 305671 3770 Valve People Playground 97.49 999 142920 1649 Studio Minus Hades 97.38 2499 199960 2829 Supergiant Games Vampire Survivors 97.37 499 130311 1624 poncle Stardew Valley 97.24 1499 497558 9283 ConcernedApe Wallpaper Engine 97.18 399 561096 11031 Wallpaper Engine Team Terraria 97.1 999 1014711 22380 Re-Logic Portal 97.0 999 111786 1752 Valve RimWorld 96.89 3499 142201 2550 Ludeon Studios Half-Life: Alyx 96.81 5999 73942 1156 Valve ULTRAKILL 96.66 2499 40050 548 New Blood Interactive Left 4 Dead 2 96.61 999 643836 16828 Valve The Henry Stickmin Collection 96.6 1499 32913 427 Innersloth The Binding of Isaac: Rebirth 96.5 1499 210521 4995 Nicalis, Inc. Helltaker 96.49 0 105952 2213 vanripper Euro Truck Simulator 2 96.48 1999 572368 15615 SCS Software Slay the Spire 96.48 849 116347 2494 Mega Crit Games Mount & Blade: Warband 96.41 499 142780 3307 TaleWorlds Entertainment Aseprite 96.4 1999 11823 80 Igara Studio Katana ZERO 96.4 899 49239 875 Devolver Digital

#### Analyse
Les meilleurs jeux, en utilisant la formule proposée sont:
1. Portal 2 (Valve)
2. People Playground (Studio Minus) [???]
3. Hades (Supergiant Games)


### Y a-t-il des années avec un nombre plus élevé de sorties ? La pandémie de Covid a-t-elle eu un impact sur le volume de publications ?

In [0]:
covid_years = [2020, 2021, 2022] # fin officielle de la pandémie en mai 2023

result_df = steam_games_df \
        .withColumn("release_year", F.year("release_date")) \
        .withColumn("is_covid", F.col("release_year").isin(covid_years)) \
        .groupBy("release_year", "is_covid").agg(F.count("*").alias("games_count"))

display(result_df \
          .orderBy(F.desc("release_year")))

release_year is_covid games_count 2022 true 7451 2021 true 8805 2020 true 8287 2019 false 6949 2018 false 7663 2017 false 6006 2016 false 4176 2015 false 2565 2014 false 1550 2013 false 469 2012 false 344 2011 false 267 2010 false 281 2009 false 309 2008 false 159 2007 false 98 2006 false 61 2005 false 6 2004 false 6 2003 false 3 2002 false 1 2001 false 4 2000 false 2 1999 false 3 1998 false 1 1997 false 2 null null 222

Databricks visualization. Run in Databricks to view.

#### Analyse

Il y a eu une forte croissance du nombre de jeux jusqu'en 2018, puis le nombre de publication est resté à peu prés stable (en moyenne) marquant ainsi une sorte de stabilisation sur la période COVID. Il faudrait les chiffres aprés 2022 pour affiner l'analyse.
On peut quand même remarquer que la première année de COVID (2019) a vu un recul par rapport à l'année précédente, avant de rebondir et surpasser le score de 2018 (adaptation à la pandémie en 2019 avec des reports ?).

Sur la base de ces données, c'est 2021, en plein COVID que l'on trouve l'année la plus prolixe (8805 publications).


### Comment les prix sont-ils répartis ?

In [0]:
prices_df = steam_games_df \
    .withColumn("price", F.col("price").cast(DoubleType()) / 100.0) \
    .withColumn("initial_price", F.col("initial_price").cast(DoubleType()) / 100.0)

In [0]:
display(prices_df)

id appid ccu categories developer genres name initial_price price discount positive_ratings negative_ratings publisher release_date has_linux_support has_mac_support has_windows_support owners languages required_age type 10 10 13990 List(Multi-player, Valve Anti-Cheat enabled, Online PvP, Shared/Split Screen PvP, PvP) Valve List(Action) Counter-Strike 9.99 9.99 0 201215 5199 Valve 2000-11-01 true true true 10,000,000 .. 20,000,000 List(English, French, German, Italian, Spanish - Spain, Simplified Chinese, Traditional Chinese, Korean) 0 game 1000000 1000000 0 List(Single-player, Partial Controller Support, Steam Achievements, Steam Cloud) IndigoBlue Game Studio List(Action, Adventure, Indie) ASCENXION 9.99 9.99 0 27 5 PsychoFlux Entertainment 2021-05-14 false false true 0 .. 20,000 List(English, Korean, Simplified Chinese) 0 game 1000010 1000010 99 List(Single-player, Partial Controller Support, Steam Achievements, Steam Cloud, Steam Trading Cards) NEXT Studios List(Adventure, Indie, RPG, Strategy) Crown Trick 19.99 5.99 70 4032 646 Team17, NEXT Studios 2020-10-16 false false true 200,000 .. 500,000 List(Simplified Chinese, English, Japanese, Traditional Chinese, French, German, Spanish - Spain, Russian, Portuguese - Brazil) 0 game 1000030 1000030 76 List(Multi-player, Single-player, Co-op, Steam Achievements, Steam Cloud, Shared/Split Screen, Full controller support, Steam Trading Cards, Shared/Split Screen Co-op, Remote Play on Phone, Remote Play on Tablet, Remote Play on TV, Remote Play Together) Vertigo Gaming Inc. List(Action, Indie, Simulation, Strategy) Cook, Serve, Delicious! 3?! 19.99 19.99 0 1575 115 Vertigo Gaming Inc. 2020-10-14 false true true 100,000 .. 200,000 List(English) 0 game 1000040 1000040 0 List(Single-player) DoubleC Games List(Action, Casual, Indie, Simulation) 细胞战争 1.99 1.99 0 0 1 DoubleC Games 2019-03-30 false false true 0 .. 20,000 List(Simplified Chinese) 0 game 1000080 1000080 3 List(Multi-player, Single-player, Steam Achievements, Full controller support, Steam Trading Cards) IndieLeague Studio List(Action, Adventure, Indie, RPG) Zengeon 19.99 7.99 60 1018 462 2P Games 2019-06-24 false true true 100,000 .. 200,000 List(Simplified Chinese, English, Traditional Chinese, Japanese, Korean) 0 game 1000100 1000100 0 List(Single-player, Steam Achievements, Steam Cloud) 七月九日 List(Adventure, Indie, RPG, Strategy) 干支セトラ　陽ノ卷｜干支etc.　陽之卷 12.99 12.99 0 18 6 Starship Studio 2019-01-24 false false true 0 .. 20,000 List(Japanese, Simplified Chinese, Traditional Chinese) 0 game 1000110 1000110 0 List(Multi-player, Single-player, Co-op, Online PvP, Online Co-op, PvP) 重庆环游者网络科技 List(Action, Adventure, Casual, Free to Play, Massively Multiplayer) Jumping Master(跳跳大咖) 0.0 0.0 0 50 34 重庆环游者网络科技 2019-04-08 false false true 20,000 .. 50,000 List(English, Simplified Chinese, Traditional Chinese) 0 game 1000130 1000130 0 List(Single-player, Steam Achievements, Steam Leaderboards) Simon Codrington List(Casual, Indie) Cube Defender 2.99 2.99 0 6 0 Simon Codrington 2019-01-06 false true true 0 .. 20,000 List(English) 0 game 1000280 1000280 0 List(Single-player) Villain Role List(Indie, RPG) Tower of Origin2-Worm's Nest 13.99 13.99 0 32 12 Villain Role 2021-09-09 false false true 0 .. 20,000 List(English, Simplified Chinese, Traditional Chinese) 0 game 1000310 1000310 0 List(Multi-player, Single-player, In-App Purchases, Online PvP, PvP) 海南众铖互娱网络科技有限公司 List(Action, RPG, Strategy) 人气动漫大乱斗 0.99 0.99 0 1 5 海南众铖互娱网络科技有限公司 2019-12-17 false false true 0 .. 20,000 List(Simplified Chinese) 0 game 1000360 1000360 59 List(Multi-player, Single-player, Shared/Split Screen, Full controller support, Shared/Split Screen PvP, Remote Play on Phone, Remote Play on Tablet, Remote Play Together, PvP) Kubold List(Action, Early Access) Hellish Quart 16.99 16.99 0 4031 315 Kubold 2021-02-16 false false true 200,000 .. 500,000 List(English, Simplified Chinese) 0 game 1000370 1000370 0 List(Single-player) LFiO Studio List(Indie) SurReal Subway 0.0 0.0 

Databricks visualization. Run in Databricks to view.

Il y a quelques "outliers" des jeux dont les tarifs sont extremement eloignés de la moyenne!

In [0]:
display(prices_df.filter(F.col("price") > 100).orderBy(F.desc("price")))

id appid ccu categories developer genres name initial_price price discount positive_ratings negative_ratings publisher release_date has_linux_support has_mac_support has_windows_support owners languages required_age type 1200520 1200520 0 List(Multi-player, Single-player, Co-op, LAN Co-op) Fury Games List(Action) Ascent Free-Roaming VR Experience 999.0 999.0 0 6 0 Fury Games 2019-12-27 false false true 0 .. 20,000 List(English) 0 game 253670 253670 0 List(Single-player) Aartform List(Animation & Modeling) Aartform Curvy 3D 3.0 299.9 299.9 0 31 13 Aartform 2013-11-12 false false true 0 .. 20,000 List(English) 0 game 502570 502570 91 List(Partial Controller Support, Steam Cloud) SideFX List(Animation & Modeling, Design & Illustration, Video Production, Game Development) Houdini Indie 269.99 269.99 0 152 8 SideFX 2018-10-10 false true true 0 .. 20,000 List(English) 0 game 2070990 2070990 2 List() MAGIX Software GmbH List(Video Production) VEGAS Edit 20 Steam Edition 249.0 249.0 0 1 0 MAGIX Software GmbH 2022-11-01 false false true 0 .. 20,000 List(English, French, German, Spanish - Spain) 0 game 1022640 1022640 0 List(Single-player) wandwand List(Casual, Indie, RPG) Lgnorant girl doll 199.99 199.99 0 2 2 wandwad 2019-02-15 false false true 0 .. 20,000 List(English) 0 game 1035340 1035340 0 List() 上海皋城软件有限公司 List(Education) 眼睛（眼球）结构研究 199.99 199.99 0 1 0 上海皋城软件有限公司 2019-03-10 false false true 0 .. 20,000 List(English, Simplified Chinese) 0 game 1103060 1103060 0 List(Single-player) H.G.G. List(Adventure, Casual, Indie, Early Access) Run Thief 199.99 199.99 0 0 2 H.G.G. 2019-08-23 false false true 0 .. 20,000 List(English, Spanish - Spain, Russian) 0 game 1259300 1259300 0 List(Single-player) Patrick Kelley, CIT List(Simulation) Spot Sample Witness Simulator 199.99 199.99 0 5 2 Kelley Integrity Safety Solutions, LLC, Endless Simulations 2020-05-26 false false true 0 .. 20,000 List(English) 0 game 1289890 1289890 0 List(Single-player) RK List(Indie, RPG, Simulation) VR Long March 199.99 199.99 0 2 1 RK 2020-11-04 false false true 0 .. 20,000 List(Simplified Chinese) 0 game 1429800 1429800 0 List(Single-player) Klip VR Immersive Technologies Pvt Ltd List(Adventure, Casual, Simulation) Chandrayaan VR 199.99 199.99 0 1 0 Klip VR 2020-12-28 false false true 0 .. 20,000 List(English) 0 game 1468060 1468060 0 List(Single-player, Steam Achievements) AssetFlipGames, ALFINA GAMERS, rocketship List(Action, Adventure, Indie) The Island of Dr. Yepstein 199.99 199.99 0 10 5 AssetFlipGames World Game Publishing, ALFINA WORLD GAME PUBLISHING, rocketship 2021-09-17 false false true 0 .. 20,000 List(English, Russian) 0 game 1538090 1538090 0 List() Virtual Human Technologies List(Indie, Simulation, Education) Virtual Orator 199.99 199.99 0 3 0 Virtual Human Technologies 2021-03-05 false false true 0 .. 20,000 List(English) 0 game 1607640 1607640 0 List(Single-player) EFatullaev List(Casual, Indie, Racing, RPG, Simulation, Sports, Early Access) Arcade Drift 199.99 199.99 0 7 1 EFatullaev 2021-06-28 false false true 0 .. 20,000 List(English) 0 game 1634660 1634660 0 List(Multi-player, Partial Controller Support, LAN PvP, PvP) rongyou List(Action, Casual) fight 199.99 199.99 0 2 1 rongyou 2021-06-01 false true false 0 .. 20,000 List(English) 0 game 1699510 1699510 0 List(Single-player) CatCat Gaming List(Indie) Reincarnation of Ocean 199.99 199.99 0 0 1 CatCat Gaming 2021-08-07 false false true 0 .. 20,000 List(English, Simplified Chinese) 0 game 1720060 1720060 0 List(Single-player) CatCat Gaming List(Simulation) Earthquake escape 199.99 199.99 0 1 2 CatCat Gaming 2021-11-25 false false true 0 .. 20,000 List(English, Simplified Chinese) 0 game 1787140 1787140 0 List(Multi-player, Shared/Split Screen, Shared/Split Screen PvP, PvP) healthy game List(Action) RagingFist 199.99 199.99 0 0 1 healthy game 2021-11-04 false false true 0 .. 20,000 List(English, Simplified Chinese) 0 game 438450 438450 4 List(Steam Trading Cards) 3Dflow SRL List(Animation & Mode

**Ascent Free-Roaming VR Experience** semble être une licence destinée à des salles d'arcade VR... On pourra éventuellement l'éliminer de nos analyses et surtout des graphiques.

In [0]:
prices_df = prices_df.filter(F.col("price") < 300).orderBy(F.desc("price"))

In [0]:
display(prices_df \
        .select("price") \
        .orderBy(F.desc("price")))

price 299.9 269.99 249.0 199.99 199.99 199.99 199.99 199.99 199.99 199.99 199.99 199.99 199.99 199.99 199.99 199.99 199.99 199.99 199.99 199.99 159.99 149.99 149.99 149.99 149.99 149.99 149.99 149.0 129.99 129.99 129.99 129.99 129.99 124.99 119.99 119.99 99.99 99.99 99.99 99.99 99.99 99.99 99.99 99.99 99.99 99.99 99.99 99.99 99.99 99.99 99.99 99.99 99.99 99.99 99.99 99.99 99.99 99.99 99.99 99.99 99.0 94.99 94.99 94.99 94.99 89.99 89.99 89.99 89.99 89.99 84.99 79.99 79.99 79.99 79.99 79.99 79.99 79.99 79.99 79.99 79.99 79.99 79.99 79.99 74.99 74.99 74.99 69.99 69.99 69.99 69.99 69.99 69.99 69.99 69.99 69.99 69.99 69.99 69.99 69.99 69.99 69.99 69.99 69.99 69.99 69.99 69.99 69.99 69.99 69.99 69.99 69.99 69.95 69.03 64.99 64.99 64.99 64.99 64.99 64.99 64.95 59.99 59.99 59.99 59.99 59.99 59.99 59.99 59.99 59.99 59.99 59.99 59.99 59.99 59.99 59.99 59.99 59.99 59.99 59.99 59.99 59.99 59.99 59.99 59.99 59.99 59.99 59.99 59.99 59.99 59.99 59.99 59.99 59.99 59.99 59.99 59.99 59.99 59.99 59.99 59.99 59.99 59.99 59.99 59.99 59.99 59.99 59.99 59.99 59.99 59.99 59.99 59.99 59.99 59.99 59.99 59.99 59.99 59.99 59.99 59.99 59.99 59.99 59.99 59.99 59.99 59.99 59.99 59.99 59.99 59.99 59.99 59.99 59.99 59.99 59.99 59.99 59.99 59.99 59.99 59.99 59.99 59.99 59.99 59.99 59.99 59.99 59.99 59.99 59.99 59.99 59.99 59.99 59.99 59.99 59.99 59.99 59.99 59.99 59.99 59.99 59.99 59.99 59.99 59.99 59.99 59.99 59.99 59.99 59.99 59.99 59.99 59.99 59.99 59.99 59.99 59.99 59.99 59.99 59.99 59.99 59.99 59.99 59.99 59.99 59.99 59.99 59.99 59.99 59.99 59.99 59.99 59.99 59.99 59.99 59.99 59.99 59.99 59.99 59.99 59.99 59.99 59.99 59.99 59.99 59.99 59.99 59.99 59.99 59.99 59.99 59.99 59.99 59.99 59.99 59.99 59.99 59.99 59.99 59.99 59.99 59.99 59.99 59.99 59.99 59.99 59.99 59.99 59.99 59.99 59.99 59.99 59.99 59.99 59.99 59.99 59.99 59.99 59.99 59.99 59.99 59.99 59.99 59.99 59.99 59.99 59.99 59.99 59.95 57.95 56.24 54.99 54.99 54.99 54.99 54.99 54.99 54.99 54.99 54.99 54.99 54.99 54.99 54.99 54.99 54.99 52.74 49.99 49.99 49.99 49.99 49.99 49.99 49.99 49.99 49.99 49.99 49.99 49.99 49.99 49.99 49.99 49.99 49.99 49.99 49.99 49.99 49.99 49.99 49.99 49.99 49.99 49.99 49.99 49.99 49.99 49.99 49.99 49.99 49.99 49.99 49.99 49.99 49.99 49.99 49.99 49.99 49.99 49.99 49.99 49.99 49.99 49.99 49.99 49.99 49.99 49.99 49.99 49.99 49.99 49.99 49.99 49.99 49.99 49.99 49.99 49.99 49.99 49.99 49.99 49.99 49.99 49.99 49.99 49.99 49.99 49.99 49.99 49.99 49.99 49.99 49.99 49.99 49.99 49.99 49.99 49.99 49.99 49.99 49.99 49.99 49.99 49.99 49.99 49.99 49.99 49.99 49.99 49.99 49.99 49.99 49.99 49.99 49.99 49.99 49.99 49.99 49.99 49.99 49.99 49.99 49.99 49.99 49.99 49.99 49.99 49.99 49.99 49.99 49.99 49.99 49.99 49.99 49.99 49.99 49.99 49.99 49.99 49.99 49.99 49.99 49.99 49.99 49.99 49.99 49.99 49.99 49.99 49.99 49.99 49.99 49.99 49.99 49.99 49.99 49.99 49.99 49.99 49.99 49.99 49.99 49.99 49.99 49.99 49.99 49.99 49.99 49.99 49.99 49.99 49.99 49.99 49.99 49.99 49.99 49.99 49.99 49.99 49.99 49.99 49.99 49.99 49.99 49.99 49.99 49.99 49.99 49.99 49.99 49.99 49.99 49.99 49.99 49.99 49.99 49.99 49.99 49.99 49.99 49.99 49.99 49.99 49.99 49.99 49.99 49.99 49.99 49.69 45.0 44.99 44.99 44.99 44.99 44.99 44.99 44.99 44.99 44.99 44.99 44.99 44.99 44.99 44.99 44.99 44.99 44.99 44.99 44.99 44.99 44.99 44.99 44.99 44.99 44.99 44.99 44.99 44.99 44.99 44.99 44.99 44.99 44.99 44.99 44.99 44.99 44.99 44.99 44.99 44.99 44.99 44.99 44.99 44.99 44.98 44.95 40.0 39.99 39.99 39.99 39.99 39.99 39.99 39.99 39.99 39.99 39.99 39.99 39.99 39.99 39.99 39.99 39.99 39.99 39.99 39.99 39.99 39.99 39.99 39.99 39.99 39.99 39.99 39.99 39.99 39.99 39.99 39.99 39.99 39.99 39.99 39.99 39.99 39.99 39.99 39.99 39.99 39.99 39.99 39.99 39.99 39.99 39.99 39.99 39.99 39.99 39.99 39.99 39.99 39.99 39.99 39.99 39.99 39.99 39.99 39.99 39.99 39.99 39.99 39.99 39.99 39.99 39.99 39.99 39.99 39.99 39.99 39.99 39.99 39.99 39.99 39.99 39.99 39.99 39.99 39.99 39.99 39.99 39.99 39.99 39.99 39.99 39.99 39.99 39.99 39.99 39.99 39.99 39.99 39.99 39.99 39.9

Databricks visualization. Run in Databricks to view.

In [0]:
result_df = steam_games_df \
    .withColumn("price", F.col("price").cast(DoubleType()) / 100.0) \
    .withColumn("initial_price", F.col("initial_price").cast(DoubleType()) / 100.0)

display(result_df.select(F.min("price").alias("min_price"), F.max("price").alias("max_price")))
# display(steam_games_df.select(F.min(F.col("price").cast(DoubleType())).alias("min_price"), F.max("price").alias("max_price")))

# width_bucket requires pyspark 3.5
# Bucket config
num_buckets = 20
min_price = 0.1
max_price = 200.0
bucket_width = (max_price - min_price) / num_buckets

# Create a new column with bucket number
result_df = result_df.withColumn(
    "bucket",
    F.width_bucket(F.col("price"), F.lit(min_price), F.lit(max_price), 20)
)

# Compute bucket label as a string, e.g., "$0.0–$20.0"
result_df = result_df.withColumn(
    "bucket_label",
    F.expr(f"""
        CASE
            WHEN bucket = 0 THEN 'Below {min_price}'
            WHEN bucket = {num_buckets + 1} THEN 'Above {max_price}'
            ELSE concat(
                '$',
                CAST({min_price} + ({bucket_width}) * (bucket - 1) AS STRING),
                '–$',
                CAST({min_price} + ({bucket_width}) * (bucket) AS STRING)
            )
        END
    """)
)

# Group by label and count
result_dist = result_df.groupBy("bucket_label").agg(F.count("*").alias("count"))

# Show result
display(result_dist.orderBy("bucket_label"))


min_price max_price 0.0 999.0

bucket_label count $0.100000000000000–$10.095000000000001 35941 $10.095000000000001–$20.090000000000002 9015 $110.045000000000011–$120.040000000000012 2 $120.040000000000012–$130.035000000000013 6 $140.030000000000014–$150.025000000000015 7 $150.025000000000015–$160.020000000000016 1 $190.005000000000019–$200.000000000000020 17 $20.090000000000002–$30.085000000000003 1789 $30.085000000000003–$40.080000000000004 600 $40.080000000000004–$50.075000000000005 238 $50.075000000000005–$60.070000000000006 206 $60.070000000000006–$70.065000000000007 34 $70.065000000000007–$80.060000000000008 16 $80.060000000000008–$90.055000000000009 6 $90.055000000000009–$100.050000000000010 29 Above 200.0 4 Below 0.1 7779

Databricks visualization. Run in Databricks to view.

In [0]:

result_df = steam_games_df \
    .withColumn("price", F.col("price").cast(DoubleType()) / 100.0) \
    .withColumn("initial_price", F.col("initial_price").cast(DoubleType()) / 100.0)

# Compute buckets with custom ranges
buckets = ["Free", "0<$<5", "5<$<10", "10<$<15", "15<$<20", "20<$<30", "30<$<50", "50<$<70", "70<$<100","Over 100"]
result_df = result_df.withColumn(
    "bucket",
    F.expr(f"""
        CASE
            WHEN price = 0 THEN 0
            WHEN price < 5 THEN 1
            WHEN price < 10 THEN 2
            WHEN price < 15 THEN 3
            WHEN price < 20 THEN 4
            WHEN price < 30 THEN 5
            WHEN price < 50 THEN 6
            WHEN price < 70 THEN 7
            WHEN price < 100 THEN 8
            ELSE 9
        END
    """)
)

# UDF (User Defined Function) qui retourne le label à partir de l'index du bucket
def get_bucket_label(bucket):
    if 0 <= bucket < len(buckets):
        return buckets[bucket]
    elif bucket >= len(buckets):
        return buckets[-1]
    else:
        return "Below range"

bucket_label_udf = F.udf(get_bucket_label, StringType())

result_df = result_df.withColumn("bucket_label", bucket_label_udf(F.col("bucket")))

# Group by label and count
result_dist = result_df.groupBy("bucket", "bucket_label").agg(F.count("*").alias("count"))

# Show result
display(result_dist.orderBy("bucket"))

bucket bucket_label count 0 Free 7779 1 0<$<5 23478 2 5<$<10 12450 3 10<$<15 5311 4 15<$<20 3711 5 20<$<30 1794 6 30<$<50 839 7 50<$<70 240 8 70<$<100 51 9 Over 100 37

Databricks visualization. Run in Databricks to view.

Databricks visualization. Run in Databricks to view.

#### Analyse

Beaucoup de jeux gratuits (14%) et encore plus à moins de 5$ (la majorité soit 42.2%).
Enfin 22% des jeux sont entre 5 et 10$.
Globalement, 78% des jeux coutent moins de 10$! De quoi s'amuser à moindre coût.


### Y a-t-il beaucoup de jeux en promotion ?

In [0]:
result_df = steam_games_df \
    .withColumn("price", F.col("price").cast(DoubleType()) / 100.0) \
    .withColumn("initial_price", F.col("initial_price").cast(DoubleType()) / 100.0)

discounted_games = result_df.filter(F.col("discount") > 0).count() #.select("discount").distinct().show()
available_games = result_df.count()

print(f"Nombre de jeux total en magasin : {available_games}")
print(f"Nombre de jeux en réduction : {discounted_games} -> {discounted_games / available_games * 100:.2f}% du total")

Nombre de jeux total en magasin : 55690
Nombre de jeux en réduction : 2518 -> 4.52% du total


#### Analyse

4.5% des jeux sont proposés avec une promotion.

### Quelles sont les langues les plus représentées ?


In [0]:
# Dans notre DataFrame, "languages" est un tableau.
# Pour pouvoir prendre en compte chaque langue, il va falloir passer par un "explode" et ainsi créer une ligne par élément du tableau.
result_df = steam_games_df \
    .withColumn("language", F.explode("languages"))

print("Top 10 des langues jouables :")
display(result_df \
    .groupBy("language").agg(F.count("*").alias("games_count")) \
    .orderBy(F.desc("games_count")) \
    .limit(15))

Top 10 des langues jouables :


language games_count English 55116 German 14019 French 13426 Russian 12922 Simplified Chinese 12782 Spanish - Spain 12233 Japanese 10368 Italian 9304 Portuguese - Brazil 6750 Korean 6600 Traditional Chinese 6307 Polish 5376 Portuguese - Portugal 4011 Turkish 3602 Dutch 3080

Databricks visualization. Run in Databricks to view.

Databricks visualization. Run in Databricks to view.

#### Analyse

Sans surprise, l'Anglais est largement en tête (quasiment tous les jeux ont une version Anglaise).
Classement :
1. English
2. German
3. French

### Combien de jeux sont interdits aux moins de 16 ou 18 ans ?

In [0]:
result_df = steam_games_df \
    .withColumn("is_16_plus", F.col("required_age") >= 16) \
    .withColumn("is_18_plus", F.col("required_age") >= 18)

# 16+ is not mixing with 18+ for clarity
is_16_plus_count = result_df.filter((F.col("is_16_plus") == True) & (F.col("is_18_plus") == False)).count()
is_16_18_plus_count = result_df.filter((F.col("is_16_plus") == True)).count()
is_18_plus_count = result_df.filter(F.col("is_18_plus") == True).count()

available_games = result_df.count()


print(f"Interdits aux moins de 16 ans: {is_16_plus_count} jeux ({is_16_plus_count / available_games * 100:.2f}% du total).")
print(f"Un total (16+ & 18+) de {is_16_18_plus_count} jeux ({is_16_18_plus_count / available_games * 100:.2f}% du total) est interdit aux moins de 16 ans.")
print(f"Interdits aux moins de 18 ans: {is_18_plus_count} jeux ({is_18_plus_count / available_games * 100:.2f}% du total).")


Interdits aux moins de 16 ans: 76 jeux (0.14% du total).
Un total (16+ & 18+) de 305 jeux (0.55% du total) est interdit aux moins de 16 ans.
Interdits aux moins de 18 ans: 229 jeux (0.41% du total).


#### Analyse
0.14% des jeux sont explicitement interdits aux moins de 16 ans.
Au total, **0.55%** des jeux seront interdits aux moins de 16 ans.

0.41% des jeux sont interdits aux moins de 18 ans.

## Analyse par genre

* Quels sont les genres les plus représentés sur la plateforme ?
* Certains genres présentent-ils de meilleurs ratios d’avis positifs/négatifs ?
* Certains éditeurs privilégient-ils des genres particuliers ?
* Quels sont les genres les plus lucratifs ?



In [0]:
# "genres" est un tableau -> explode
steam_games_genres_df = steam_games_df.withColumn('genre', F.explode('genres'))

### Quels sont les genres les plus représentés sur la plateforme ?

In [0]:
# Total number of games: 55690
display(steam_games_genres_df \
    .groupBy("genre").agg(F.count("*").alias("games_count")) \
    .withColumn("ratio", 100 * F.col("games_count") / 55690) \
    .orderBy(F.desc("games_count")) \
    .limit(10))


genre games_count ratio Indie 39681 71.25336685221764 Action 23759 42.662955647333455 Casual 22086 39.65882564194649 Adventure 21431 38.48267193391992 Strategy 10895 19.563655952594722 Simulation 10836 19.457712336146525 RPG 9534 17.119770156221943 Early Access 6145 11.034297001256958 Free to Play 3393 6.092655773029269 Sports 2666 4.7872149398455734

Databricks visualization. Run in Databricks to view.

Databricks visualization. Run in Databricks to view.

#### Analyse

71% des jeux sont des jeux indépendants.

42% des jeux sont des jeux d'action.

### Certains genres présentent-ils de meilleurs ratios d’avis positifs/négatifs ?

In [0]:
# Note: un jeu peu être multi catégoriel
# Compute rating ratios per genre
result_df = steam_games_genres_df.groupBy("genre") \
    .agg((F.sum("positive_ratings")/F.sum("negative_ratings")).alias("ratings_ratio"))

display(result_df.orderBy(F.desc("ratings_ratio")).limit(10))


genre ratings_ratio Photo Editing 42.03353946889778 Animation & Modeling 26.17327220369809 Design & Illustration 24.958603325063873 Utilities 16.99503482518447 Game Development 8.38759926695174 Indie 7.67017877344188 Audio Production 7.331141281289775 7.078350594848496 Video Production 6.815425987043149 Casual 6.527673915758578

Databricks visualization. Run in Databricks to view.

#### Analyse

Le genre **Photo Editing** offre le meilleur ratio.

### Certains éditeurs privilégient-ils des genres particuliers ?

In [0]:
from pyspark.sql.window import Window

# Aggregate over publisher
wPublisher  = Window.partitionBy("publisher")

# Limit to publisher with more than 50 games
result_df = steam_games_genres_df \
        .select(F.coalesce("publisher", "developer").alias("publisher"), "genre") \
        .withColumn("games_count", F.count("*").over(wPublisher)) \
        .filter(F.col("games_count") > 50) \
        .groupBy("publisher", "genre", "games_count") \
        .agg((F.count("*")/F.col("games_count")).alias("genre_ratio"), F.count("*").alias("genre_games_count")) \
        .orderBy(F.desc("genre_ratio"))

display(result_df)

publisher genre games_count genre_ratio genre_games_count 8floor Casual 243 0.831275720164609 202 MangaGamer Adventure 66 0.6818181818181818 45 Reforged Group Indie 135 0.6518518518518519 88 Slitherine Ltd. Strategy 162 0.6049382716049383 98 William at Oxford Casual 88 0.5795454545454546 51 Humongous Entertainment, Nightdive Studios Casual 56 0.5714285714285714 32 Zoo Corporation Casual 55 0.5454545454545454 30 MumboJumbo Casual 63 0.5396825396825397 34 ImperiumGame Indie 75 0.5333333333333333 40 familyplay Casual 66 0.5303030303030303 35 Capcom Action 62 0.5161290322580645 32 Bethesda Softworks Action 73 0.5068493150684932 37 8Floor Casual 83 0.5060240963855421 42 Big Fish Games Casual 836 0.5011961722488039 419 Artifex Mundi Casual 150 0.4866666666666667 73 EnsenaSoft Casual 66 0.48484848484848486 32 Blender Games Casual 145 0.4827586206896552 70 Blender Games Indie 145 0.4827586206896552 70 Winged Cloud Simulation 58 0.4827586206896552 28 Artifex Mundi Adventure 150 0.48 72 Big Fish Games Adventure 836 0.4700956937799043 393 BANDAI NAMCO Entertainment Action 111 0.46846846846846846 52 Warner Bros. Interactive Entertainment Action 54 0.46296296296296297 25 NIS America, Inc. RPG 66 0.45454545454545453 30 kovalevviktor Indie 73 0.4520547945205479 33 Laush Studio Indie 276 0.4492753623188406 124 khukhrovr Indie 65 0.4461538461538462 29 Piko Interactive LLC, Bleem! Action 72 0.4444444444444444 32 Luci Entertainment Indie 79 0.4430379746835443 35 Rebellion Action 57 0.43859649122807015 25 For Kids Casual 73 0.4383561643835616 32 For Kids Indie 73 0.4383561643835616 32 Jackbox Games, Inc. Indie 53 0.4339622641509434 23 MAGIX Software GmbH Video Production 83 0.43373493975903615 36 Paradox Interactive Strategy 130 0.4307692307692308 56 Humongous Entertainment, Nightdive Studios Adventure 56 0.42857142857142855 24 NanningsGames Casual 59 0.423728813559322 25 Luci Entertainment Casual 79 0.4177215189873418 33 Deep Silver Action 60 0.4166666666666667 25 Jackbox Games, Inc. Casual 53 0.41509433962264153 22 Minimol Games Casual 64 0.40625 26 Disney Action 69 0.4057971014492754 28 Activision Action 69 0.4057971014492754 28 Disney Adventure 69 0.4057971014492754 28 DigiPen Institute of Technology Action 63 0.3968253968253968 25 Sokpop Collective Indie 248 0.3911290322580645 97 Kagura Games RPG 200 0.39 78 HH-Games Casual 340 0.38823529411764707 132 ebi-hime Indie 57 0.38596491228070173 22 OTAKU Plan RPG 73 0.3835616438356164 28 W.T.B. Indie 60 0.38333333333333336 23 ANPA.US Indie 84 0.38095238095238093 32 DigiPen Institute of Technology Free to Play 63 0.38095238095238093 24 Kagura Games Indie 200 0.38 76 Henteko Doujin Action 61 0.3770491803278688 23 Raw Fury Indie 75 0.37333333333333335 28 Annapurna Interactive Adventure 57 0.3684210526315789 21 Pixel Games UK Action 79 0.3670886075949367 29 Bitlock Studio Indie 90 0.36666666666666664 33 Garage Games Indie 153 0.3660130718954248 56 PLAYISM Indie 223 0.3632286995515695 81 Aerosoft GmbH Simulation 91 0.3626373626373626 33 Sometimes You Indie 130 0.36153846153846153 47 Henteko Doujin Indie 61 0.36065573770491804 22 Snkl Studio Casual 78 0.358974358974359 28 Snkl Studio Indie 78 0.358974358974359 28 Digital Tribe Indie 67 0.3582089552238806 24 Gamera Games Indie 73 0.3561643835616438 26 Daedalic Entertainment Indie 187 0.35294117647058826 66 Back To Basics Gaming Indie 151 0.3509933774834437 53 Tero Lunkka Indie 194 0.35051546391752575 68 Piko Interactive LLC, Bleem! Adventure 72 0.3472222222222222 25 United Independent Entertainment Simulation 107 0.34579439252336447 37 OTAKU Plan Adventure 73 0.3424657534246575 25 Quarlellle Indie 76 0.34210526315789475 26 Kalypso Media Digital Strategy 82 0.34146341463414637 28 Capcom Adventure 62 0.3387096774193548 21 MACKINN7 Indie 62 0.3387096774193548 21 MAGIX Software GmbH Audio Production 83 0.3373493975903614 28 Annapurna Interactive Indie 57 0.3333333333333333 19 Fellow Traveller Indie 54 0.3333333333333333 18 Paradise Project Indie 66 0.33333333

#### Analyse

Pas vraiment pertinent comme analyse. Certains éditeurs ont effectivement un genre prédominant (casual gaming chez 8floor).

Notons également que beaucoup de jeux sont multi-genres.



### Quels sont les genres les plus lucratifs ?

In [0]:
# Besoin du nombre de copies -> approximation avec le minimum/maximum du range "owners" ?
steam_games_genres_df.select("owners").distinct().show()

+--------------------+
|              owners|
+--------------------+
|  100,000 .. 200,000|
|1,000,000 .. 2,00...|
|20,000,000 .. 50,...|
|5,000,000 .. 10,0...|
|         0 .. 20,000|
|    20,000 .. 50,000|
|2,000,000 .. 5,00...|
|50,000,000 .. 100...|
|200,000,000 .. 50...|
|500,000 .. 1,000,000|
|10,000,000 .. 20,...|
|  200,000 .. 500,000|
|   50,000 .. 100,000|
+--------------------+



In [0]:
# Besoin du nombre de copies -> approximation avec le minimum/maximum du range "owners" ?
result_df = steam_games_genres_df \
    .withColumn("price", F.col("price").cast(DoubleType()) / 100.0) \
    .withColumn("owners", F.split(F.col("owners"),  "\s*[\.]+\s*")) \
    .withColumn("min_owners", F.replace(F.col("owners").getItem(0), F.lit(","), F.lit("")).cast(IntegerType())) \
    .withColumn("max_owners", F.replace(F.col("owners").getItem(1), F.lit(","), F.lit("")).cast(IntegerType())) \
    .withColumn("min_revenue", F.round(F.col("min_owners") * F.col("price"), 2)) \
    .withColumn("max_revenue", F.round(F.col("max_owners") * F.col("price"), 2)) \
    .withColumn("industry_min_revenue", F.sum("min_revenue").over(Window.partitionBy()))

# display(result_df)

result_df = result_df \
    .groupBy("genre", "industry_min_revenue") \
    .agg(F.sum("min_revenue").alias("total_min_revenue"), F.sum("max_revenue").alias("total_max_revenue")) \
    .withColumn("ratio_over_industry", F.round(100 * F.col("total_min_revenue") / F.col("industry_min_revenue"), 2)) \
    .orderBy(F.col("total_min_revenue").desc()) \
    .limit(10)

display(result_df)


genre industry_min_revenue total_min_revenue total_max_revenue ratio_over_industry Action 1.338739392E11 3.59292701E10 8.15836381E10 26.84 Adventure 1.338739392E11 2.26189065E10 5.18725704E10 16.9 Indie 1.338739392E11 1.9134717E10 4.55584372E10 14.29 RPG 1.338739392E11 1.66751283E10 3.76711579E10 12.46 Strategy 1.338739392E11 1.23623921E10 2.793769E10 9.23 Simulation 1.338739392E11 1.14222333E10 2.61172658E10 8.53 Casual 1.338739392E11 4.4765685E9 1.16853448E10 3.34 Massively Multiplayer 1.338739392E11 3.6927213E9 8.1675942E9 2.76 Early Access 1.338739392E11 3.1470668E9 7.7702561E9 2.35 Sports 1.338739392E11 1.8160534E9 4.4837413E9 1.36

Databricks visualization. Run in Databricks to view.

#### Analyse

Une grosse partie des revenus (26% des revenus du catalogue Steam) semble être captée par les jeux d'action.

## Analyse par plateforme

* La majorité des jeux sont-ils disponibles sur Windows, Mac ou Linux ?
* Certains genres sont-ils plus souvent disponibles sur certaines plateformes ?

In [0]:
steam_games_platforms_df = steam_games_genres_df \
    .withColumn("total_games_count", F.count("*").over(Window.partitionBy()))

### La majorité des jeux sont-ils disponibles sur Windows, Mac ou Linux ?

In [0]:
result_df = steam_games_platforms_df \
    .groupBy("has_windows_support", "has_mac_support", "has_linux_support", "total_games_count") \
    .agg(F.count("*").alias("games_count")) \
    .withColumn("total_games_ratio", F.round(100 * F.col("games_count") / F.col("total_games_count"), 2)) \
    .orderBy(F.desc("has_windows_support"), F.desc("has_mac_support"), F.desc("has_linux_support"))

display(result_df.select("has_windows_support", "has_mac_support", "has_linux_support", "games_count", "total_games_ratio"))

has_windows_support has_mac_support has_linux_support games_count total_games_ratio true true true 19388 12.33 true true false 16535 10.51 true false true 4636 2.95 true false false 116675 74.19 false true true 3 0.0 false true false 30 0.02 false false true 3 0.0

In [0]:
result_df = steam_games_platforms_df \
    .agg(
        F.sum(F.col("has_linux_support").cast(IntegerType())).alias("linux_count"),
        F.sum(F.col("has_mac_support").cast(IntegerType())).alias("mac_count"),
        F.sum(F.col("has_windows_support").cast(IntegerType())).alias("windows_count"),
        F.max(F.col("total_games_count")).alias("total_games_count")
    ) \
    .withColumn("linux_games_ratio", F.round(100 * F.col("linux_count") / F.col("total_games_count"), 2)) \
    .withColumn("mac_games_ratio", F.round(100 * F.col("mac_count") / F.col("total_games_count"), 2)) \
    .withColumn("windows_games_ratio", F.round(100 * F.col("windows_count") / F.col("total_games_count"), 2))

display(result_df)

linux_count mac_count windows_count total_games_count linux_games_ratio mac_games_ratio windows_games_ratio 24030 35956 157234 157270 15.28 22.86 99.98

#### Analyse

- Quasiment 100% des jeux disponibles sur Steam supportent Windows.
- 22% tournent sur Mac.
- 15% supportent Linux.


### Certains genres sont-ils plus souvent disponibles sur certaines plateformes ?

In [0]:
result_df = steam_games_genres_df \
    .groupBy('genre') \
    .agg(
        F.sum(F.col('has_linux_support').cast('int')).alias('linux_count'),
        F.sum(F.col('has_mac_support').cast('int')).alias('mac_count'),
        F.sum(F.col('has_windows_support').cast('int')).alias('windows_count')
    )

display(result_df)

genre linux_count mac_count windows_count Education 19 56 317 Massively Multiplayer 164 270 1459 Sexual Content 7 13 54 Adventure 3302 5039 21427 Sports 287 506 2665 Accounting 0 4 16 Audio Production 7 41 193 Video Production 6 29 247 Animation & Modeling 38 74 322 Racing 304 424 2154 Gore 14 20 99 Design & Illustration 54 100 405 Software Training 12 27 164 Web Publishing 8 20 89 Photo Editing 4 16 105 Utilities 49 102 681 Violent 22 33 168 Game Development 35 52 159 Movie 0 0 1 Nudity 7 10 45 Early Access 632 900 6145 Casual 3305 5130 22082 41 54 158 Action 3379 4564 23755 Strategy 1826 3005 10892 Indie 6978 9935 39676 Free to Play 474 845 3391 RPG 1524 2248 9533 Simulation 1532 2439 10832

#### Analyse

On peut voir que les jeux sont d'abord sur Windows, ensuite Maci puis Linux.